<a href="https://colab.research.google.com/github/skywalker0803r/NLP/blob/main/bert.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# setup

In [1]:
!pip install transformers tqdm boto3 requests regex -q

In [2]:
import torch
from transformers import BertTokenizer
from IPython.display import clear_output

In [3]:
PRETRAINED_MODEL_NAME = "bert-base-chinese"  # 指定繁簡中文 BERT-BASE 預訓練模型
# 取得此預訓練模型所使用的 tokenizer
tokenizer = BertTokenizer.from_pretrained(PRETRAINED_MODEL_NAME)

clear_output()
print("PyTorch 版本：", torch.__version__)

PyTorch 版本： 1.8.0+cu101


In [4]:
vocab = tokenizer.vocab
print("字典大小：", len(vocab))

字典大小： 21128


# 有 ## 前綴的 tokens 即為 wordpieces。 將本來的 words 拆成更小粒度的 wordpieces

In [5]:
import random
random_tokens = random.sample(list(vocab), 10)
random_ids = [vocab[t] for t in random_tokens]

print("{0:20}{1:15}".format("token", "index"))
print("-" * 25)
for t, id in zip(random_tokens, random_ids):
    print("{0:15}{1:10}".format(t, id))

token               index          
-------------------------
51                   8246
狱                    4328
籮                    5099
勁                    1233
##武                 16693
遣                    6897
菌                    5826
abs                  8494
march                9581
##▫                 13608


# 利用中文 BERT 的 tokenizer 將一個中文句子斷詞看看

In [6]:
text = "[CLS] 等到潮水 [MASK] 了，就知道誰沒穿褲子。"
tokens = tokenizer.tokenize(text)
ids = tokenizer.convert_tokens_to_ids(tokens)
print(text)
print(tokens[:10], '...')
print(ids[:10], '...')

[CLS] 等到潮水 [MASK] 了，就知道誰沒穿褲子。
['[CLS]', '等', '到', '潮', '水', '[MASK]', '了', '，', '就', '知'] ...
[101, 5023, 1168, 4060, 3717, 103, 749, 8024, 2218, 4761] ...


# 現在馬上讓我們看看給定上面有 [MASK] 的句子，BERT 會填入什麼字

net forward

In [7]:
from transformers import BertForMaskedLM

tokens_tensor = torch.tensor([ids])  # (1, seq_len)
segments_tensors = torch.zeros_like(tokens_tensor)  # (1, seq_len)
maskedLM_model = BertForMaskedLM.from_pretrained(PRETRAINED_MODEL_NAME)
clear_output()

maskedLM_model.eval()
with torch.no_grad():
    outputs = maskedLM_model(tokens_tensor, segments_tensors)
    predictions = outputs[0]
    # (1, seq_len, num_hidden_units)
del maskedLM_model

Post-processing

In [8]:
# 將 [MASK] 位置的機率分佈取 top k 最有可能的 tokens 出來
masked_index = 5
k = 3
probs, indices = torch.topk(torch.softmax(predictions[0, masked_index], -1), k)
predicted_tokens = tokenizer.convert_ids_to_tokens(indices.tolist())

# 顯示 top k 可能的字。一般我們就是取 top 1 當作預測值
print("輸入 tokens ：", tokens[:10], '...')
print('-' * 50)
for i, (t, p) in enumerate(zip(predicted_tokens, probs), 1):
    tokens[masked_index] = t
    print("Top {} ({:2}%)：{}".format(i, int(p.item() * 100), tokens[:10]), '...')

輸入 tokens ： ['[CLS]', '等', '到', '潮', '水', '[MASK]', '了', '，', '就', '知'] ...
--------------------------------------------------
Top 1 (67%)：['[CLS]', '等', '到', '潮', '水', '來', '了', '，', '就', '知'] ...
Top 2 (25%)：['[CLS]', '等', '到', '潮', '水', '濕', '了', '，', '就', '知'] ...
Top 3 ( 2%)：['[CLS]', '等', '到', '潮', '水', '過', '了', '，', '就', '知'] ...


* 學會填克漏字讓 BERT 更好地 model 每個詞彙在不同語境下該有的 repr.，而 NSP 任務則能幫助 BERT model 兩個句子之間的關係，這在問答系統 QA、自然語言推論 NLI 或是後面我們會看到的假新聞分類任務都很有幫助。
* 這樣的 word repr. 就是近年十分盛行的 contextual word representation 概念。跟以往沒有蘊含上下文資訊的 Word2Vec、GloVe 等無語境的詞嵌入向量有很大的差異。用稍微學術一點的說法就是：

* Contextual word repr. 讓同 word type 的 word token 在不同語境下有不同的表示方式；而傳統的詞向量無論上下文，都會讓同 type 的 word token 的 repr. 相同。

* 直覺上 contextual word representation 比較能反映人類語言的真實情況，畢竟同個詞彙的含義在不同情境下相異是再正常不過的事情。在不同語境下給同個詞彙相同的 word repr. 這件事情在近年的 NLP 領域裡頭顯得越來越不合理。

* 情境 1：胖虎叫大雄去買漫畫，回來慢了就打他。

* 情境 2：妹妹說胖虎是「胖子」，他聽了很不開心。

很明顯地，在這兩個情境裡頭「他」所代表的語義以及指稱的對象皆不同。如果仍使用沒蘊含上下文 / 語境資訊的詞向量，機器就會很難正確地「解讀」這兩個句子所蘊含的語義了。

現在讓我們跟隨這個 Colab 筆記本安裝 BERT 的視覺化工具 BertViz，看看 BERT 會怎麼處理這兩個情境：

In [9]:
# 安裝 BertViz
import sys
!test -d bertviz_repo || git clone https://github.com/jessevig/bertviz bertviz_repo
if not 'bertviz_repo' in sys.path:
  sys.path += ['bertviz_repo']

# import packages
from transformers import BertTokenizer, BertModel
from bertviz import head_view

In [10]:
# 在 jupyter notebook 裡頭顯示 visualzation 的 helper
def call_html():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              "d3": "https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.8/d3.min",
              jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
            },
          });
        </script>
        '''))

clear_output()

Setup 以後就能非常輕鬆地將 BERT 內部的注意力機制視覺化出來：

In [11]:
# 記得我們是使用中文 BERT
model_version = 'bert-base-chinese'
model = BertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = BertTokenizer.from_pretrained(model_version)

def plot_attention(sentence_a,sentence_b):
  # 得到 tokens 後丟入 BERT 取得 attention
  inputs = tokenizer.encode_plus(sentence_a, sentence_b, return_tensors='pt', add_special_tokens=True)
  # 取得注意力
  token_type_ids = inputs['token_type_ids']
  input_ids = inputs['input_ids']
  attention = model(input_ids, token_type_ids=token_type_ids)[-1]
  input_id_list = input_ids[0].tolist() # Batch index 0
  tokens = tokenizer.convert_ids_to_tokens(input_id_list)
  # 交給 BertViz 視覺化
  call_html()
  head_view(attention, tokens)

In [12]:
# 情境 1 的句子
sentence_a = "胖虎叫大雄去買漫畫，"
sentence_b = "回來慢了就打他。"
plot_attention(sentence_a,sentence_b)

<IPython.core.display.Javascript object>

In [13]:
# 情境 2 的句子
sentence_a = "妹妹說胖虎是「胖子」,"
sentence_b = "他聽了很不開心。"
plot_attention(sentence_a,sentence_b)

<IPython.core.display.Javascript object>

* 假如你仍然似懂非懂，只需記得：
  BERT 是一個強大的語言代表模型，給它一段文本序列，它能回傳一段相同長度且蘊含上下文資訊 word repr. 序列，對下游的 NLP 任務很有幫助。

有了這樣的概念以後，我們接下來要做的事情很簡單，
* 1. 就是將自己感興趣的 NLP 任務的文本丟入 BERT ，為文本裡頭的每個 token 取得有語境的 word repr.
* 2. 以此 repr. 進一步 fine tune 當前任務，取得更好的結果。

# 用 BERT fine tune 下游任務

假新聞分類任務

![img](https://leemeng.tw/images/nlp-kaggle-intro/view-data-on-kaggle.jpg)

給定假新聞 title1，判斷另一新聞 title2 跟 title1 的關係（同意、反對或無關)

fine tune BERT 來解決新的下游任務有 5 個簡單步驟

* 1.準備原始文本數據 網址(https://www.kaggle.com/c/fake-news-pair-classification-challenge/data)
* 2.將原始文本轉換成 BERT 相容的輸入格式
* 3.在 BERT 之上加入新 layer 成下游任務模型
* 4.訓練該下游任務模型
* 5.對新樣本做推論

# 1.準備原始文本數據

In [14]:
import os
import pandas as pd
os.getcwd()

'/content'

In [16]:
train_file_path = '/content/drive/MyDrive/kaggle/fake-news-pair-classification-challenge/train.csv'
test_file_path = '/content/drive/MyDrive/kaggle/fake-news-pair-classification-challenge/test.csv'

# 簡單的數據清理，去除空白標題的 examples
df_train = pd.read_csv(train_file_path)
empty_title = ((df_train['title2_zh'].isnull()) \
               | (df_train['title1_zh'].isnull()) \
               | (df_train['title2_zh'] == '') \
               | (df_train['title2_zh'] == '0'))
df_train = df_train[~empty_title]

# 剔除過長的樣本以避免 BERT 無法將整個輸入序列放入記憶體不多的 GPU
MAX_LENGTH = 30
df_train = df_train[~(df_train.title1_zh.apply(lambda x : len(x)) > MAX_LENGTH)]
df_train = df_train[~(df_train.title2_zh.apply(lambda x : len(x)) > MAX_LENGTH)]

# 只用 1% 訓練數據看看 BERT 對少量標註數據有多少幫助
SAMPLE_FRAC = 0.01
df_train = df_train.sample(frac=SAMPLE_FRAC, random_state=9527)

# 去除不必要的欄位並重新命名兩標題的欄位名
df_train = df_train.reset_index()
df_train = df_train.loc[:, ['title1_zh', 'title2_zh', 'label']]
df_train.columns = ['text_a', 'text_b', 'label']

# idempotence, 將處理結果另存成 tsv 供 PyTorch 使用
df_train.to_csv("train.tsv", sep="\t", index=False)

print("訓練樣本數：", len(df_train))
df_train.head()

訓練樣本數： 2657


text_a                          text_b      label
0       苏有朋要结婚了，但网友觉得他还是和林心如比较合适  好闺蜜结婚给不婚族的秦岚扔花球，倒霉的秦岚掉水里笑哭苏有朋！  unrelated
1  爆料李小璐要成前妻了贾乃亮模仿王宝强一步到位、快刀斩乱麻！  李小璐要变前妻了？贾乃亮可能效仿王宝强当机立断，快刀斩乱麻！     agreed
2  为彩礼，母亲把女儿嫁给陌生男子，十年后再见面，母亲湿了眼眶  阿姨，不要彩礼是觉得你家穷，给你台阶下，不要以为我嫁不出去！  unrelated
3         猪油是个宝，一勺猪油等于十副药，先备起来再说  传承千百的猪油为何变得人人唯恐避之不及？揭开猪油的四大谣言！  unrelated
4                  剖析：香椿，为什么会致癌？            香椿含亚硝酸盐多吃会致癌？测完发现是谣言  disagreed